In [1]:
from sklearn.decomposition import PCA
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.cross_decomposition import PLSRegression
from sklearn.metrics import explained_variance_score
from sklearn.model_selection import train_test_split 
from sklearn.decomposition import KernelPCA
from sklearn.kernel_approximation import Nystroem
from sklearn.decomposition import PCA
from sklearn.pipeline import Pipeline
from sklearn.metrics import mean_squared_error, r2_score
import elapid
from elapid import MaxentModel
from sklearn.model_selection import GroupKFold, GridSearchCV
import pickle
from sklearn.metrics import make_scorer
from sklearn.model_selection import cross_validate
from sklearn.metrics import accuracy_score
from sklearn.metrics import roc_auc_score, f1_score, precision_score, recall_score, balanced_accuracy_score

import joblib


In [2]:
combined_df_nans = pd.read_parquet("/cluster/home/maikents/sinmod_features_masters/dataframes_pipeline_6/total_df_with_nans_and_labels.parquet")


In [3]:
combined_df_no_nans = combined_df_nans.dropna()

In [2]:
#If using spatial block cv:
X_train_raw = pd.read_csv("/cluster/home/maikents/sinmod_features_masters/ready_for_training/pipeline6/X_train_spatial.csv")
X_test_raw = pd.read_csv("/cluster/home/maikents/sinmod_features_masters/ready_for_training/pipeline6/X_test_spatial.csv")
y_train = pd.read_csv("/cluster/home/maikents/sinmod_features_masters/ready_for_training/pipeline6/y_train_spatial.csv")
y_test = pd.read_csv("/cluster/home/maikents/sinmod_features_masters/ready_for_training/pipeline6/y_test_spatial.csv")
groups_train = pd.read_csv("/cluster/home/maikents/sinmod_features_masters/ready_for_training/pipeline6/groups_train_spatial.csv")
groups_test = pd.read_csv("/cluster/home/maikents/sinmod_features_masters/ready_for_training/pipeline6/groups_test_spatial.csv")

In [3]:
pls = PLSRegression(n_components=2)
pls.fit(X_train_raw , y_train)

PLSRegression()

In [4]:
X_scores, Y_scores = pls.transform(X_train_raw), pls.predict(X_train_raw)

In [5]:
Y_train_pred = pls.predict(X_train_raw)
Y_test_pred = pls.predict(X_test_raw)


In [6]:
X_train_pls = pls.transform(X_train_raw)
X_test_pls = pls.transform(X_test_raw)

In [7]:
print(X_train_pls)

[[ 2.44225859  0.27742146]
 [ 1.47283291  0.02313216]
 [ 1.11685951 -2.69928348]
 ...
 [ 0.4468451   0.74519167]
 [ 1.56461944  0.75042532]
 [-1.55421139  0.54418338]]


In [8]:
model = elapid.MaxentModel()
gkf = GroupKFold(n_splits=6)
cv_splits = list(gkf.split(X_train_pls, y_train, groups=groups_train))

param_grid = {
    'beta_multiplier': [0.5, 1.0, 2.0, 3.0, 4.0],
    'beta_hinge': [0.5, 1.0, 1.5, 2.0],
    'beta_threshold': [0.5, 1.0, 1.5, 2.0]
}

cv_model = GridSearchCV(
    estimator=model,
    param_grid=param_grid,
    cv=cv_splits,
    scoring={'ROC': make_scorer(roc_auc_score, needs_proba=True)},
    refit='ROC',
    return_train_score=True
)

cv_model.fit(X_train_pls, y_train)

/cluster/home/maikents/PyEnvCoralMapping/lib/python3.12/site-packages/sklearn/metrics/_scorer.py:610: FutureWarning: The `needs_threshold` and `needs_proba` parameter are deprecated in version 1.4 and will be removed in 1.6. You can either let `response_method` be `None` or set it to `predict` to preserve the same behaviour.
  warnings.warn(
/cluster/home/maikents/PyEnvCoralMapping/lib/python3.12/site-packages/sklearn/model_selection/_validation.py:1000: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/cluster/home/maikents/PyEnvCoralMapping/lib/python3.12/site-packages/sklearn/metrics/_scorer.py", line 139, in __call__
    score = scorer._score(
            ^^^^^^^^^^^^^^
  File "/cluster/home/maikents/PyEnvCoralMapping/lib/python3.12/site-packages/sklearn/metrics/_scorer.py", line 371, in _score
    y_pred = method_caller(
             ^^^^^^^^^^^^^^
  File "/cluster/home

GridSearchCV(cv=[(array([   0,    1,    2, ..., 1949, 1951, 1953]),
                  array([   3,    5,   11,   16,   23,   28,   29,   31,   32,   35,   37,
         38,   39,   40,   45,   50,   52,   53,   56,   69,   79,   81,
         82,   85,   88,   92,   93,  102,  109,  116,  123,  125,  130,
        131,  133,  136,  138,  139,  145,  146,  148,  151,  153,  155,
        163,  171,  178,  179,  186,  188,  190,  195,  196,  201,  203,
        206,  209,  210,  211,  212,  223,  224,  228,  230,  236,  239,
        241,  245,  253,  257,  274,  280,  283,  290,  292,  294,  298,
        301,  307,  310,...
       1464, 1514, 1537, 1542, 1575, 1598, 1610, 1625, 1637, 1641, 1692,
       1703, 1725, 1728, 1763, 1768, 1770, 1847, 1874, 1908, 1909, 1911,
       1913]))],
             estimator=MaxentModel(),
             param_grid={'beta_hinge': [0.5, 1.0, 1.5, 2.0],
                         'beta_multiplier': [0.5, 1.0, 2.0, 3.0, 4.0],
                         'beta_threshold': [0.5, 1.0, 1.5, 2.0]},
             refit='ROC', return_train_score=True,
             scoring={'ROC': make_scorer(roc_auc_score, response_method='predict_proba')})

In [9]:
y_pred_test = cv_model.predict(X_test_pls)


In [10]:
best_model = cv_model.best_estimator_


In [11]:
y_train_pred = best_model.predict_proba(X_train_pls)[:, 1]

train_auc_score = roc_auc_score(y_train, y_train_pred)

print(f"Train AUC: {train_auc_score:.3f}")


Train AUC: 0.873


In [12]:

y_test_pred = best_model.predict_proba(X_test_pls)[:, 1]

auc_score = roc_auc_score(y_test, y_test_pred)

print(f"Test AUC: {auc_score:.3f}")
print("Best regularization parameters found:", cv_model.best_params_)

Test AUC: 0.850
Best regularization parameters found: {'beta_hinge': 0.5, 'beta_multiplier': 0.5, 'beta_threshold': 0.5}


In [4]:
pca = PCA(n_components=0.95)
X_train = pca.fit_transform(X_train_raw)

X_test = pca.transform(X_test_raw)

In [18]:
model = elapid.MaxentModel()

gkf = GroupKFold(n_splits=6)
cv_splits = list(gkf.split(X_train, y_train, groups=groups_train))

param_grid = {
    'beta_multiplier': [0.5, 1.0, 2.0, 3.0, 4.0],
    'beta_hinge': [0.5, 1.0, 1.5, 2.0],
    'beta_threshold': [0.5, 1.0, 1.5, 2.0]
}

cv_model = GridSearchCV(
    estimator=model,
    param_grid=param_grid,
    cv=cv_splits,
    scoring={'ROC': make_scorer(roc_auc_score, needs_proba=True)},
    refit='ROC',
    return_train_score=True
)

cv_model.fit(X_train, y_train)

/cluster/home/maikents/PyEnvCoralMapping/lib/python3.12/site-packages/sklearn/metrics/_scorer.py:610: FutureWarning: The `needs_threshold` and `needs_proba` parameter are deprecated in version 1.4 and will be removed in 1.6. You can either let `response_method` be `None` or set it to `predict` to preserve the same behaviour.
  warnings.warn(
/cluster/home/maikents/PyEnvCoralMapping/lib/python3.12/site-packages/sklearn/model_selection/_validation.py:1000: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/cluster/home/maikents/PyEnvCoralMapping/lib/python3.12/site-packages/sklearn/metrics/_scorer.py", line 139, in __call__
    score = scorer._score(
            ^^^^^^^^^^^^^^
  File "/cluster/home/maikents/PyEnvCoralMapping/lib/python3.12/site-packages/sklearn/metrics/_scorer.py", line 371, in _score
    y_pred = method_caller(
             ^^^^^^^^^^^^^^
  File "/cluster/home

GridSearchCV(cv=[(array([   0,    1,    2, ..., 1949, 1951, 1953]),
                  array([   3,    5,   11,   16,   23,   28,   29,   31,   32,   35,   37,
         38,   39,   40,   45,   50,   52,   53,   56,   69,   79,   81,
         82,   85,   88,   92,   93,  102,  109,  116,  123,  125,  130,
        131,  133,  136,  138,  139,  145,  146,  148,  151,  153,  155,
        163,  171,  178,  179,  186,  188,  190,  195,  196,  201,  203,
        206,  209,  210,  211,  212,  223,  224,  228,  230,  236,  239,
        241,  245,  253,  257,  274,  280,  283,  290,  292,  294,  298,
        301,  307,  310,...
       1464, 1514, 1537, 1542, 1575, 1598, 1610, 1625, 1637, 1641, 1692,
       1703, 1725, 1728, 1763, 1768, 1770, 1847, 1874, 1908, 1909, 1911,
       1913]))],
             estimator=MaxentModel(),
             param_grid={'beta_hinge': [0.5, 1.0, 1.5, 2.0],
                         'beta_multiplier': [0.5, 1.0, 2.0, 3.0, 4.0],
                         'beta_threshold': [0.5, 1.0, 1.5, 2.0]},
             refit='ROC', return_train_score=True,
             scoring={'ROC': make_scorer(roc_auc_score, response_method='predict_proba')})

In [21]:
joblib.dump(cv_model, '/cluster/home/maikents/maxent_model_pipeline_7.pkl')


['/cluster/home/maikents/maxent_model_pipeline_7.pkl']

In [5]:
cv_model = joblib.load('/cluster/home/maikents/maxent_model_pipeline_7.pkl')


In [6]:
best_model = cv_model.best_estimator_

In [11]:
#Predict probabilities on the training set
y_train_pred = best_model.predict_proba(X_train)[:, 1]

train_auc_score = roc_auc_score(y_train, y_train_pred)

print(f"Train AUC: {train_auc_score:.3f}")


Train AUC: 0.866


In [ ]:

x_coords = combined_df_nans['x']
y_coords = combined_df_nans['y']

X_grid_raw = combined_df_nans.drop(columns=['x', 'y', 'labels', 'chlor_a_10th_percentile', 'sediment_nitrate_mean',
'sediment_nitrate_90th_percentile', 'temperature_max', 'salinity_10th_percentile', 'salinity_90th_percentile',
'current_speed_90th_percentile', 'chlor_a_90th_percentile', 'sediment_silicate_mean'], errors='ignore')
X_grid_clean = X_grid_raw.dropna()
valid_idx = X_grid_clean.index

X_grid_pca = pca.transform(X_grid_clean)

# Chunked prediction
chunk_size = 2000
num_chunks = int(np.ceil(len(X_grid_pca) / chunk_size))
predicted_probabilities_list = []

for i in range(num_chunks):
    start = i * chunk_size
    end = min((i + 1) * chunk_size, len(X_grid_pca))
    chunk = X_grid_pca[start:end]
    probs = best_model.predict_proba(chunk)[:, 1]
    predicted_probabilities_list.append(probs)

# Combine results
predicted_probs = np.concatenate(predicted_probabilities_list)


In [7]:
X_grid_clean = combined_df_no_nans.drop(columns=['x', 'y', 'labels', 'chlor_a_10th_percentile', 'sediment_nitrate_mean',
'sediment_nitrate_90th_percentile', 'temperature_max', 'salinity_10th_percentile', 'salinity_90th_percentile',
'current_speed_90th_percentile', 'chlor_a_90th_percentile', 'sediment_silicate_mean'], errors='ignore')


In [8]:
#Evaluate the test performance
best_model = cv_model.best_estimator_

y_test_pred = best_model.predict_proba(X_test)[:, 1]

auc_score = roc_auc_score(y_test, y_test_pred)

print(f"Test AUC: {auc_score:.3f}")
print("Best regularization parameters found:", cv_model.best_params_)

Test AUC: 0.844
Best regularization parameters found: {'beta_hinge': 0.5, 'beta_multiplier': 0.5, 'beta_threshold': 0.5}


In [5]:
from sklearn.kernel_approximation import Nystroem
from sklearn.decomposition import PCA

feature_map = Nystroem(kernel='rbf', gamma=0.1, n_components=50)
X_train_mapped = feature_map.fit_transform(X_train_raw)

pca = PCA(n_components=9)
X_train_kpca = pca.fit_transform(X_train_mapped)


In [6]:
X_test_mapped = feature_map.transform(X_test_raw)
X_test_kpca = pca.transform(X_test_mapped)

In [7]:
model = elapid.MaxentModel()
gkf = GroupKFold(n_splits=6)
cv_splits = list(gkf.split(X_train_kpca, y_train, groups=groups_train))

param_grid = {
    'beta_multiplier': [0.5, 1.0, 2.0, 3.0, 4.0],
    'beta_hinge': [0.5, 1.0, 1.5, 2.0],
    'beta_threshold': [0.5, 1.0, 1.5, 2.0]
}

cv_model = GridSearchCV(
    estimator=model,
    param_grid=param_grid,
    cv=cv_splits,
    scoring={'ROC': make_scorer(roc_auc_score, needs_proba=True)},
    refit='ROC',
    return_train_score=True
)

cv_model.fit(X_train_kpca, y_train)

/cluster/home/maikents/PyEnvCoralMapping/lib/python3.12/site-packages/sklearn/metrics/_scorer.py:610: FutureWarning: The `needs_threshold` and `needs_proba` parameter are deprecated in version 1.4 and will be removed in 1.6. You can either let `response_method` be `None` or set it to `predict` to preserve the same behaviour.
  warnings.warn(
/cluster/home/maikents/PyEnvCoralMapping/lib/python3.12/site-packages/sklearn/model_selection/_validation.py:1000: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/cluster/home/maikents/PyEnvCoralMapping/lib/python3.12/site-packages/sklearn/metrics/_scorer.py", line 139, in __call__
    score = scorer._score(
            ^^^^^^^^^^^^^^
  File "/cluster/home/maikents/PyEnvCoralMapping/lib/python3.12/site-packages/sklearn/metrics/_scorer.py", line 371, in _score
    y_pred = method_caller(
             ^^^^^^^^^^^^^^
  File "/cluster/home

GridSearchCV(cv=[(array([   0,    1,    2, ..., 1949, 1951, 1953]),
                  array([   3,    5,   11,   16,   23,   28,   29,   31,   32,   35,   37,
         38,   39,   40,   45,   50,   52,   53,   56,   69,   79,   81,
         82,   85,   88,   92,   93,  102,  109,  116,  123,  125,  130,
        131,  133,  136,  138,  139,  145,  146,  148,  151,  153,  155,
        163,  171,  178,  179,  186,  188,  190,  195,  196,  201,  203,
        206,  209,  210,  211,  212,  223,  224,  228,  230,  236,  239,
        241,  245,  253,  257,  274,  280,  283,  290,  292,  294,  298,
        301,  307,  310,...
       1464, 1514, 1537, 1542, 1575, 1598, 1610, 1625, 1637, 1641, 1692,
       1703, 1725, 1728, 1763, 1768, 1770, 1847, 1874, 1908, 1909, 1911,
       1913]))],
             estimator=MaxentModel(),
             param_grid={'beta_hinge': [0.5, 1.0, 1.5, 2.0],
                         'beta_multiplier': [0.5, 1.0, 2.0, 3.0, 4.0],
                         'beta_threshold': [0.5, 1.0, 1.5, 2.0]},
             refit='ROC', return_train_score=True,
             scoring={'ROC': make_scorer(roc_auc_score, response_method='predict_proba')})

In [8]:
best_model = cv_model.best_estimator_


In [9]:
y_train_pred = best_model.predict_proba(X_train_kpca)[:, 1]

train_auc_score = roc_auc_score(y_train, y_train_pred)

print(f"Train AUC: {train_auc_score:.3f}")


Train AUC: 0.898


In [10]:
y_test_pred = best_model.predict_proba(X_test_kpca)[:, 1]

auc_score = roc_auc_score(y_test, y_test_pred)

print(f"Test AUC: {auc_score:.3f}")
print("Best regularization parameters found:", cv_model.best_params_)

Test AUC: 0.876
Best regularization parameters found: {'beta_hinge': 0.5, 'beta_multiplier': 0.5, 'beta_threshold': 0.5}
